In [1]:
cd /home/yuchen/pulse2percept

/home/yuchen/pulse2percept


In [2]:
from pulse2percept.models import BiphasicAxonMapModel, AxonMapModel
from pulse2percept.model_selection import ParticleSwarmOptimizer
from pulse2percept.implants import ArgusII
import shapes
import pandas as pd
import pickle
import matplotlib.pyplot as plt
import numpy as np

In [4]:
s2 = shapes.subject_params['12-005']
implant, model = shapes.model_from_params(s2)
model.xystep=0.5

estimator = shapes.BiphasicAxonMapEstimator(implant=implant, model=model,resize=True, threshold='compute', loss_fn='r2',mse_params=['area','orientation',"major_axis_length", "minor_axis_length"])
search_params = {
    'rho': (10, 1000),
    'axlambda': (10, 2500)
}
opt = ParticleSwarmOptimizer(estimator, search_params, max_iter=100, swarm_size=20, has_loss_function=True)

data = shapes.load_shapes("/home/yuchen/shapes/data/shapes.h5", subjects=['12-005'], stim_class=None)
data = data[data['electrode2'] == str()].reset_index(drop=True)
x = data[['amp1', 'freq', 'pdur', 'electrode1']]
y = data['image']

y_moments = estimator.compute_moments(y)
averaged_moments = data
averaged_moments[['area', 'eccentricity', 'orientation','compactness']] = y_moments
averaged_moments = averaged_moments.groupby(['amp1', 'freq', 'electrode1','pdur'])['area', 'eccentricity', 'orientation','compactness'].mean()
x = averaged_moments.index.to_frame().reset_index(drop=True)

train_mse = []
test_mse = []
train_size = []
test_size = []
estimator_params = []
filename_lst = []
electrode_lst=[]  # in case the server disconnects when program is running

for electrode in x.electrode1.unique():
    if electrode not in electrode_lst:
        estimator = shapes.BiphasicAxonMapEstimator(implant=implant, model=model,resize=True, threshold='compute', loss_fn='r2',mse_params=['area','orientation',"major_axis_length", "minor_axis_length"])
        y_moments = estimator.compute_moments(y)
        averaged_moments = data
        averaged_moments[['area', 'eccentricity', 'orientation','compactness']] = y_moments
        averaged_moments = averaged_moments.groupby(['amp1', 'freq', 'electrode1','pdur'])['area', 'eccentricity', 'orientation','compactness'].mean()
        # generate filename
        filename = 'Biphasic_' + 's2_' + electrode + '.pickle'
        filename_lst.append(filename)

        # get train_x and train_y
        train_x = x[x.electrode1 != electrode].reset_index(drop=True)
        train_y = averaged_moments.drop(electrode,level=2, axis=0)
        train_size.append(len(train_x))
        
        # fitting and finding the best parameter
        best_mse = 0
        best_score = 99999
        best_estimator = estimator
        for itr in range(3):
            print("Now we are fitting: " + filename[:-7] + " round " + str(itr))
            opt = ParticleSwarmOptimizer(estimator, search_params, max_iter=100, swarm_size=20, has_loss_function=True)
            estimator.fit_size_model(data['amp1'], y)
            opt.fit(train_x, train_y)
            score = estimator.score(train_x, train_y,return_mses=True)
            if score[0]<best_score: 
                best_score = score[0]
                best_estimator = estimator
                best_mse = score[1]

        # store train results and estimator
        train_mse.append([best_score,best_mse])
        estimator = best_estimator
        pickle.dump(estimator, open("/home/yuchen/shapes/estimator05xystep/" + filename, 'wb'))
        estimator_params.append(estimator.get_params())
        
        # test (recompute y moments)
        estimator.mse_params = ['moments_central', "area", "eccentricity", "major_axis_length", "minor_axis_length", "orientation"]
        estimator.scale_features=True
        y_moments = pd.DataFrame(estimator.compute_moments(y, fit_scaler=True))
        result = pd.concat([y_moments, data[['amp1', 'freq', 'electrode1','pdur']]], axis=1, join='inner')
        test_y = result.groupby(['amp1', 'freq', 'electrode1','pdur']).mean().loc[pd.IndexSlice[:, :,electrode], :]
        test_x = x[x.electrode1 == electrode].reset_index(drop=True)

        # store test results
        test_size.append(len(test_x))
        test_mse.append(estimator.score(test_x, test_y, return_mses=True))
        
        rho = []
        axlambda = []
        a5 = []
        train_MSE_combined = []
        train_MSE_area = []
        train_MSE_major_axis_length = []
        train_MSE_minor_axis_length = []

        test_MSE_combined = []
        test_MSE_M00 = []
        test_MSE_M02 = []
        test_MSE_M11 = []
        test_MSE_M12 = []
        test_MSE_M20 = []
        test_MSE_M21 = []
        test_MSE_M22 = []

        test_MSE_area = []
        test_MSE_eccentricity = []
        test_MSE_major_axis_length = []
        test_MSE_minor_axis_length = []
        test_MSE_orientation = []


        rho.append(estimator_params[-1]['rho'])
        axlambda.append(estimator_params[-1]['axlambda'])
        a5.append(estimator_params[-1]['a5'])
        train_MSE_combined.append(train_mse[-1][0])
        train_MSE_area.append(train_mse[-1][1][0])
        train_MSE_major_axis_length.append(train_mse[-1][1][1])
        train_MSE_minor_axis_length.append(train_mse[-1][1][2])
        
        test_MSE_combined.append(test_mse[-1][0])
        test_MSE_M00.append(test_mse[-1][1][0])
        test_MSE_M02.append(test_mse[-1][1][1])
        test_MSE_M11.append(test_mse[-1][1][2])
        test_MSE_M12.append(test_mse[-1][1][3])
        test_MSE_M20.append(test_mse[-1][1][4])
        test_MSE_M21.append(test_mse[-1][1][5])
        test_MSE_M22.append(test_mse[-1][1][6])

        test_MSE_area.append(test_mse[-1][1][7])
        test_MSE_eccentricity.append(test_mse[-1][1][8])    
        test_MSE_major_axis_length.append(test_mse[-1][1][9])
        test_MSE_minor_axis_length.append(test_mse[-1][1][10])
        test_MSE_orientation.append(test_mse[-1][1][11])

        df = pd.DataFrame({'electrode':[electrode],
                       'rho':rho,
                       'axlambda':axlambda,
                        'a5':a5,
                       'train_combined':train_MSE_combined,
                       'train_area':train_MSE_area,
                       'train_MSE_major_axis_length':train_MSE_major_axis_length,
                       'train_MSE_minor_axis_length':train_MSE_minor_axis_length,

                       'test_combined':test_MSE_combined,
                       'test_M00':test_MSE_M00,
                       'test_M02':test_MSE_M02,
                       'test_M11':test_MSE_M11,
                       'test_M12':test_MSE_M12,
                       'test_M20':test_MSE_M20,
                       'test_M21':test_MSE_M21,
                       'test_M22':test_MSE_M22,
                       'test_area':test_MSE_area,
                       'test_eccentricity':test_MSE_eccentricity,
                       'test_major_axis_length':test_MSE_major_axis_length,
                       'test_minor_axis_length':test_MSE_minor_axis_length,
                       'test_orientation':test_MSE_orientation,


                        'train_size': [train_size[-1]],
                      'test_size':[test_size[-1]],
                      'filename':filename})
        df.to_csv("/home/yuchen/shapes/estimator05xystep/" + filename[:-7] + '.csv', encoding='utf-8') 

Removing means (['area: 671.25', 'orientation: 0.13', 'major_axis_length: 56.65', 'minor_axis_length: 20.53']) 
Scaling standard deviations (['area: 541.86', 'orientation: 0.94', 'major_axis_length: 28.77', 'minor_axis_length: 10.46']) to be 1
Removing means (['area: 671.25', 'orientation: 0.13', 'major_axis_length: 56.65', 'minor_axis_length: 20.53']) 
Scaling standard deviations (['area: 541.86', 'orientation: 0.94', 'major_axis_length: 28.77', 'minor_axis_length: 10.46']) to be 1
Now we are fitting: Biphasic_s2_A1 round 0
a5=0.315505, a6=0.368989
score:153.769, rho:435.5, lambda:2310.2, a5:0.316, empty:0, scores: ['area:117.3', 'orientation:1.8', 'major_axis_length:15.2', 'minor_axis_length:19.4']
score:90.561, rho:391.8, lambda:1665.9, a5:0.316, empty:0, scores: ['area:65.1', 'orientation:1.7', 'major_axis_length:9.8', 'minor_axis_length:13.9']
score:447.891, rho:686.5, lambda:1816.1, a5:0.316, empty:0, scores: ['area:365.7', 'orientation:1.9', 'major_axis_length:20.8', 'minor_axis

In [5]:
s3 = shapes.subject_params['51-009']
implant, model = shapes.model_from_params(s3)
model.xystep=0.5

estimator = shapes.BiphasicAxonMapEstimator(implant=implant, model=model,resize=True, threshold='compute', loss_fn='r2',mse_params=['area','orientation',"major_axis_length", "minor_axis_length"])
search_params = {
    'rho': (10, 1000),
    'axlambda': (10, 2500)
}
opt = ParticleSwarmOptimizer(estimator, search_params, max_iter=100, swarm_size=20, has_loss_function=True)

data = shapes.load_shapes("/home/yuchen/shapes/data/shapes.h5", subjects=['51-009'], stim_class=None)
data = data[data['electrode2'] == str()].reset_index(drop=True)
x = data[['amp1', 'freq', 'pdur', 'electrode1']]
y = data['image']

y_moments = estimator.compute_moments(y)
averaged_moments = data
averaged_moments[['area', 'eccentricity', 'orientation','compactness']] = y_moments
averaged_moments = averaged_moments.groupby(['amp1', 'freq', 'electrode1','pdur'])['area', 'eccentricity', 'orientation','compactness'].mean()
x = averaged_moments.index.to_frame().reset_index(drop=True)

train_mse = []
test_mse = []
train_size = []
test_size = []
estimator_params = []
filename_lst = []
electrode_lst=[]  # in case the server disconnects when program is running

for electrode in x.electrode1.unique():
    if electrode not in electrode_lst:
        estimator = shapes.BiphasicAxonMapEstimator(implant=implant, model=model,resize=True, threshold='compute', loss_fn='r2',mse_params=['area','orientation',"major_axis_length", "minor_axis_length"])
        y_moments = estimator.compute_moments(y)
        averaged_moments = data
        averaged_moments[['area', 'eccentricity', 'orientation','compactness']] = y_moments
        averaged_moments = averaged_moments.groupby(['amp1', 'freq', 'electrode1','pdur'])['area', 'eccentricity', 'orientation','compactness'].mean()
        # generate filename
        filename = 'Biphasic_' + 's3_' + electrode + '.pickle'
        filename_lst.append(filename)

        # get train_x and train_y
        train_x = x[x.electrode1 != electrode].reset_index(drop=True)
        train_y = averaged_moments.drop(electrode,level=2, axis=0)
        train_size.append(len(train_x))
        
        # fitting and finding the best parameter
        best_mse = 0
        best_score = 99999
        best_estimator = estimator
        for itr in range(3):
            print("Now we are fitting: " + filename[:-7] + " round " + str(itr))
            opt = ParticleSwarmOptimizer(estimator, search_params, max_iter=100, swarm_size=20, has_loss_function=True)
            estimator.fit_size_model(data['amp1'], y)
            opt.fit(train_x, train_y)
            score = estimator.score(train_x, train_y,return_mses=True)
            if score[0]<best_score: 
                best_score = score[0]
                best_estimator = estimator
                best_mse = score[1]

        # store train results and estimator
        train_mse.append([best_score,best_mse])
        estimator = best_estimator
        pickle.dump(estimator, open("/home/yuchen/shapes/estimator05xystep/" + filename, 'wb'))
        estimator_params.append(estimator.get_params())
        
        # test (recompute y moments)
        estimator.mse_params = ['moments_central', "area", "eccentricity", "major_axis_length", "minor_axis_length", "orientation"]
        estimator.scale_features=True
        y_moments = pd.DataFrame(estimator.compute_moments(y, fit_scaler=True))
        result = pd.concat([y_moments, data[['amp1', 'freq', 'electrode1','pdur']]], axis=1, join='inner')
        test_y = result.groupby(['amp1', 'freq', 'electrode1','pdur']).mean().loc[pd.IndexSlice[:, :,electrode], :]
        test_x = x[x.electrode1 == electrode].reset_index(drop=True)

        # store test results
        test_size.append(len(test_x))
        test_mse.append(estimator.score(test_x, test_y, return_mses=True))
        
        rho = []
        axlambda = []
        a5 = []
        train_MSE_combined = []
        train_MSE_area = []
        train_MSE_major_axis_length = []
        train_MSE_minor_axis_length = []

        test_MSE_combined = []
        test_MSE_M00 = []
        test_MSE_M02 = []
        test_MSE_M11 = []
        test_MSE_M12 = []
        test_MSE_M20 = []
        test_MSE_M21 = []
        test_MSE_M22 = []

        test_MSE_area = []
        test_MSE_eccentricity = []
        test_MSE_major_axis_length = []
        test_MSE_minor_axis_length = []
        test_MSE_orientation = []


        rho.append(estimator_params[-1]['rho'])
        axlambda.append(estimator_params[-1]['axlambda'])
        a5.append(estimator_params[-1]['a5'])
        train_MSE_combined.append(train_mse[-1][0])
        train_MSE_area.append(train_mse[-1][1][0])
        train_MSE_major_axis_length.append(train_mse[-1][1][1])
        train_MSE_minor_axis_length.append(train_mse[-1][1][2])
        
        test_MSE_combined.append(test_mse[-1][0])
        test_MSE_M00.append(test_mse[-1][1][0])
        test_MSE_M02.append(test_mse[-1][1][1])
        test_MSE_M11.append(test_mse[-1][1][2])
        test_MSE_M12.append(test_mse[-1][1][3])
        test_MSE_M20.append(test_mse[-1][1][4])
        test_MSE_M21.append(test_mse[-1][1][5])
        test_MSE_M22.append(test_mse[-1][1][6])

        test_MSE_area.append(test_mse[-1][1][7])
        test_MSE_eccentricity.append(test_mse[-1][1][8])    
        test_MSE_major_axis_length.append(test_mse[-1][1][9])
        test_MSE_minor_axis_length.append(test_mse[-1][1][10])
        test_MSE_orientation.append(test_mse[-1][1][11])

        df = pd.DataFrame({'electrode':[electrode],
                       'rho':rho,
                       'axlambda':axlambda,
                        'a5':a5,
                       'train_combined':train_MSE_combined,
                       'train_area':train_MSE_area,
                       'train_MSE_major_axis_length':train_MSE_major_axis_length,
                       'train_MSE_minor_axis_length':train_MSE_minor_axis_length,

                       'test_combined':test_MSE_combined,
                       'test_M00':test_MSE_M00,
                       'test_M02':test_MSE_M02,
                       'test_M11':test_MSE_M11,
                       'test_M12':test_MSE_M12,
                       'test_M20':test_MSE_M20,
                       'test_M21':test_MSE_M21,
                       'test_M22':test_MSE_M22,
                       'test_area':test_MSE_area,
                       'test_eccentricity':test_MSE_eccentricity,
                       'test_major_axis_length':test_MSE_major_axis_length,
                       'test_minor_axis_length':test_MSE_minor_axis_length,
                       'test_orientation':test_MSE_orientation,


                        'train_size': [train_size[-1]],
                      'test_size':[test_size[-1]],
                      'filename':filename})
        df.to_csv("/home/yuchen/shapes/estimator05xystep/" + filename[:-7] + '.csv', encoding='utf-8')

Removing means (['area: 176.1', 'orientation: -0.18', 'major_axis_length: 65.07', 'minor_axis_length: 6.25']) 
Scaling standard deviations (['area: 97.11', 'orientation: 0.76', 'major_axis_length: 35.65', 'minor_axis_length: 3.54']) to be 1
Removing means (['area: 176.1', 'orientation: -0.18', 'major_axis_length: 65.07', 'minor_axis_length: 6.25']) 
Scaling standard deviations (['area: 97.11', 'orientation: 0.76', 'major_axis_length: 35.65', 'minor_axis_length: 3.54']) to be 1
Now we are fitting: Biphasic_s3_B4 round 0
a5=0.066319, a6=0.867362
score:1653.648, rho:395.5, lambda:1005.0, a5:0.066, empty:0, scores: ['area:1363.0', 'orientation:3.2', 'major_axis_length:1.0', 'minor_axis_length:286.5']
score:797.391, rho:243.3, lambda:1650.8, a5:0.066, empty:0, scores: ['area:682.5', 'orientation:2.3', 'major_axis_length:1.1', 'minor_axis_length:111.5']
score:373.660, rho:319.3, lambda:162.1, a5:0.066, empty:0, scores: ['area:204.1', 'orientation:2.9', 'major_axis_length:1.4', 'minor_axis_le

In [6]:
s4 = shapes.subject_params['52-001']
implant, model = shapes.model_from_params(s4)
model.xystep=0.5

estimator = shapes.BiphasicAxonMapEstimator(implant=implant, model=model,resize=True, threshold='compute', loss_fn='r2',mse_params=['area','orientation',"major_axis_length", "minor_axis_length"])
search_params = {
    'rho': (10, 1000),
    'axlambda': (10, 2500)
}
opt = ParticleSwarmOptimizer(estimator, search_params, max_iter=100, swarm_size=20, has_loss_function=True)

data = shapes.load_shapes("/home/yuchen/shapes/data/shapes.h5", subjects=['52-001'], stim_class=None)
data = data[data['electrode2'] == str()].reset_index(drop=True)
x = data[['amp1', 'freq', 'pdur', 'electrode1']]
y = data['image']

y_moments = estimator.compute_moments(y)
averaged_moments = data
averaged_moments[['area', 'eccentricity', 'orientation','compactness']] = y_moments
averaged_moments = averaged_moments.groupby(['amp1', 'freq', 'electrode1','pdur'])['area', 'eccentricity', 'orientation','compactness'].mean()
x = averaged_moments.index.to_frame().reset_index(drop=True)

train_mse = []
test_mse = []
train_size = []
test_size = []
estimator_params = []
filename_lst = []
electrode_lst=[]  # in case the server disconnects when program is running

for electrode in x.electrode1.unique():
    if electrode not in electrode_lst:
        estimator = shapes.BiphasicAxonMapEstimator(implant=implant, model=model,resize=True, threshold='compute', loss_fn='r2',mse_params=['area','orientation',"major_axis_length", "minor_axis_length"])
        y_moments = estimator.compute_moments(y)
        averaged_moments = data
        averaged_moments[['area', 'eccentricity', 'orientation','compactness']] = y_moments
        averaged_moments = averaged_moments.groupby(['amp1', 'freq', 'electrode1','pdur'])['area', 'eccentricity', 'orientation','compactness'].mean()
        # generate filename
        filename = 'Biphasic_' + 's4_' + electrode + '.pickle'
        filename_lst.append(filename)

        # get train_x and train_y
        train_x = x[x.electrode1 != electrode].reset_index(drop=True)
        train_y = averaged_moments.drop(electrode,level=2, axis=0)
        train_size.append(len(train_x))
        
        # fitting and finding the best parameter
        best_mse = 0
        best_score = 99999
        best_estimator = estimator
        for itr in range(3):
            print("Now we are fitting: " + filename[:-7] + " round " + str(itr))
            opt = ParticleSwarmOptimizer(estimator, search_params, max_iter=100, swarm_size=20, has_loss_function=True)
            estimator.fit_size_model(data['amp1'], y)
            opt.fit(train_x, train_y)
            score = estimator.score(train_x, train_y,return_mses=True)
            if score[0]<best_score: 
                best_score = score[0]
                best_estimator = estimator
                best_mse = score[1]

        # store train results and estimator
        train_mse.append([best_score,best_mse])
        estimator = best_estimator
        pickle.dump(estimator, open("/home/yuchen/shapes/estimator05xystep/" + filename, 'wb'))
        estimator_params.append(estimator.get_params())
        
        # test (recompute y moments)
        estimator.mse_params = ['moments_central', "area", "eccentricity", "major_axis_length", "minor_axis_length", "orientation"]
        estimator.scale_features=True
        y_moments = pd.DataFrame(estimator.compute_moments(y, fit_scaler=True))
        result = pd.concat([y_moments, data[['amp1', 'freq', 'electrode1','pdur']]], axis=1, join='inner')
        test_y = result.groupby(['amp1', 'freq', 'electrode1','pdur']).mean().loc[pd.IndexSlice[:, :,electrode], :]
        test_x = x[x.electrode1 == electrode].reset_index(drop=True)

        # store test results
        test_size.append(len(test_x))
        test_mse.append(estimator.score(test_x, test_y, return_mses=True))
        
        rho = []
        axlambda = []
        a5 = []
        train_MSE_combined = []
        train_MSE_area = []
        train_MSE_major_axis_length = []
        train_MSE_minor_axis_length = []

        test_MSE_combined = []
        test_MSE_M00 = []
        test_MSE_M02 = []
        test_MSE_M11 = []
        test_MSE_M12 = []
        test_MSE_M20 = []
        test_MSE_M21 = []
        test_MSE_M22 = []

        test_MSE_area = []
        test_MSE_eccentricity = []
        test_MSE_major_axis_length = []
        test_MSE_minor_axis_length = []
        test_MSE_orientation = []


        rho.append(estimator_params[-1]['rho'])
        axlambda.append(estimator_params[-1]['axlambda'])
        a5.append(estimator_params[-1]['a5'])
        train_MSE_combined.append(train_mse[-1][0])
        train_MSE_area.append(train_mse[-1][1][0])
        train_MSE_major_axis_length.append(train_mse[-1][1][1])
        train_MSE_minor_axis_length.append(train_mse[-1][1][2])
        
        test_MSE_combined.append(test_mse[-1][0])
        test_MSE_M00.append(test_mse[-1][1][0])
        test_MSE_M02.append(test_mse[-1][1][1])
        test_MSE_M11.append(test_mse[-1][1][2])
        test_MSE_M12.append(test_mse[-1][1][3])
        test_MSE_M20.append(test_mse[-1][1][4])
        test_MSE_M21.append(test_mse[-1][1][5])
        test_MSE_M22.append(test_mse[-1][1][6])

        test_MSE_area.append(test_mse[-1][1][7])
        test_MSE_eccentricity.append(test_mse[-1][1][8])    
        test_MSE_major_axis_length.append(test_mse[-1][1][9])
        test_MSE_minor_axis_length.append(test_mse[-1][1][10])
        test_MSE_orientation.append(test_mse[-1][1][11])

        df = pd.DataFrame({'electrode':[electrode],
                       'rho':rho,
                       'axlambda':axlambda,
                        'a5':a5,
                       'train_combined':train_MSE_combined,
                       'train_area':train_MSE_area,
                       'train_MSE_major_axis_length':train_MSE_major_axis_length,
                       'train_MSE_minor_axis_length':train_MSE_minor_axis_length,

                       'test_combined':test_MSE_combined,
                       'test_M00':test_MSE_M00,
                       'test_M02':test_MSE_M02,
                       'test_M11':test_MSE_M11,
                       'test_M12':test_MSE_M12,
                       'test_M20':test_MSE_M20,
                       'test_M21':test_MSE_M21,
                       'test_M22':test_MSE_M22,
                       'test_area':test_MSE_area,
                       'test_eccentricity':test_MSE_eccentricity,
                       'test_major_axis_length':test_MSE_major_axis_length,
                       'test_minor_axis_length':test_MSE_minor_axis_length,
                       'test_orientation':test_MSE_orientation,


                        'train_size': [train_size[-1]],
                      'test_size':[test_size[-1]],
                      'filename':filename})
        df.to_csv("/home/yuchen/shapes/estimator05xystep/" + filename[:-7] + '.csv', encoding='utf-8')

Removing means (['area: 1283.73', 'orientation: 0.16', 'major_axis_length: 115.9', 'minor_axis_length: 32.69']) 
Scaling standard deviations (['area: 1504.13', 'orientation: 0.88', 'major_axis_length: 106.19', 'minor_axis_length: 34.74']) to be 1
Removing means (['area: 1283.73', 'orientation: 0.16', 'major_axis_length: 115.9', 'minor_axis_length: 32.69']) 
Scaling standard deviations (['area: 1504.13', 'orientation: 0.88', 'major_axis_length: 106.19', 'minor_axis_length: 34.74']) to be 1
Now we are fitting: Biphasic_s4_A5 round 0
a5=0.645419, a6=-0.290838
score:55.610, rho:782.8, lambda:903.8, a5:0.645, empty:0, scores: ['area:45.3', 'orientation:3.9', 'major_axis_length:1.1', 'minor_axis_length:5.3']
score:4.919, rho:227.8, lambda:807.8, a5:0.645, empty:0, scores: ['area:0.5', 'orientation:2.2', 'major_axis_length:1.4', 'minor_axis_length:0.9']
score:4.994, rho:245.7, lambda:1541.4, a5:0.645, empty:0, scores: ['area:0.7', 'orientation:2.3', 'major_axis_length:1.2', 'minor_axis_length